In [1]:
import sys
# sys.path.append('/Users/udodehm/workspace/models/slim')
sys.path.append('./util')
sys.path.append('./scripts_cnn_models_slim')
import os
import urllib.request as urllib
import numpy as np
import tensorflow as tf
from tensorflow.contrib import slim

%matplotlib inline
import matplotlib.pyplot as plt

# from nets import vgg
# from nets import resnet_v1 as resnet
import vgg
import resnet_v1 as resnet
import cnn_model as cnnm
import nn_helpers as nnhelp

import plot_helpers as plt_help
import download


urls = ["http://download.tensorflow.org/models/vgg_16_2016_08_28.tar.gz",
        'http://download.tensorflow.org/models/resnet_v1_50_2016_08_28.tar.gz']
checkpoints_dir = './models/slim/checkpoints'
graphs_dir = './models/slim/graphs/'

for url in urls:
    download.maybe_download_and_extract(url=url, 
                                        download_dir=checkpoints_dir,
                                        print_download_progress=False)

Data has apparently already been downloaded and unpacked.
Data has apparently already been downloaded and unpacked.


# Resnet up-projection

In [2]:
tf.reset_default_graph()
image_size = resnet.resnet_v1_50.default_image_size
print('default image size: {}'.format(image_size))
batch_size = 4
shape = [batch_size] + [320, 320, 3]

# input for cnn:
x = tf.placeholder(dtype=tf.float32, 
                   shape=shape, 
                   name='input')
is_training = tf.placeholder(dtype=tf.bool, name='is_training')

default image size: 224


In [3]:
bn_decay = 0.999
bn_epsilon = 0.001

with tf.Graph().as_default():    
    # Create the model, use the default arg scope to configure the batch norm parameters.
    with slim.arg_scope(resnet.resnet_arg_scope()):
        # 1000 classes instead of 1001.
        scope = 'resnet_v1_50'
        net, end_points = resnet.resnet_v1_50(inputs=x,
                                              num_classes=None,
                                              is_training=is_training,
                                              global_pool=False,
                                              output_stride=None,
                                              spatial_squeeze=False,
                                              reuse=None,
                                              scope=scope)
        print(net)

    with tf.variable_scope(name_or_scope='decoder', default_name='decoder',
                           values=[net]) as sc:
        end_points_collection = sc.name + '_end_points'
        # Collect outputs for conv2d, fully_connected and max_pool2d.
        with slim.arg_scope(cnnm.upproject_arg_scope(weight_decay=0.0001,
                                                     batch_norm_decay=bn_decay,
                                                     batch_norm_epsilon=bn_epsilon,
                                                     batch_norm_scale=True,
                                                     activation_fn=None,
                                                     use_batch_norm=True,
                                                     is_training=is_training)):
            with slim.arg_scope([slim.conv2d],
                                outputs_collections=end_points_collection):
                net = slim.conv2d(inputs=net,
                                  num_outputs=1024,
                                  kernel_size=[1, 1],
                                  stride=1,
                                  padding='SAME',
                                  data_format='NHWC', 
                                  trainable=True,
                                  scope='conv1')

        net = cnnm.up_project(input_data=net, kernel_size=[3, 3], num_outputs=512, 
                              batch_size=batch_size, scope='2x_up_projection', stride=1,
                              use_batch_norm=True, bn_decay=bn_decay,
                              bn_epsilon=bn_epsilon, is_training=is_training)
        print(net)
        net = cnnm.up_project(input_data=net, kernel_size=[3, 3], num_outputs=256, 
                              batch_size=batch_size, scope='4x_up_projection', stride=1,
                              use_batch_norm=True, bn_decay=bn_decay,
                              bn_epsilon=bn_epsilon, is_training=is_training)
        net = cnnm.up_project(input_data=net, kernel_size=[3, 3], num_outputs=128, 
                              batch_size=batch_size, scope='8x_up_projection', stride=1,
                              use_batch_norm=True, bn_decay=bn_decay,
                              bn_epsilon=bn_epsilon, is_training=is_training)
        net = cnnm.up_project(input_data=net, kernel_size=[3, 3], num_outputs=64, 
                              batch_size=batch_size, scope='16x_up_projection', stride=1, 
                              use_batch_norm=True, bn_decay=bn_decay,
                              bn_epsilon=bn_epsilon, is_training=is_training)
#         with slim.arg_scope(cnnm.upproject_arg_scope(weight_decay=0.0001,
#                                                      batch_norm_decay=bn_decay,
#                                                      batch_norm_epsilon=bn_epsilon,
#                                                      batch_norm_scale=True,
#                                                      activation_fn=None,
#                                                      use_batch_norm=True,
#                                                      is_training=is_training)):
#             with slim.arg_scope([slim.conv2d],
#                                 outputs_collections=end_points_collection):
#                 net_albedo = slim.conv2d(inputs=net,
#                                          num_outputs=3,
#                                          kernel_size=[3, 3],
#                                          stride=1,
#                                          padding='SAME',
#                                          data_format='NHWC', 
#                                          trainable=True,
#                                          scope='conv2_albedo')

#                 net_shading = slim.conv2d(inputs=net,
#                                           num_outputs=3,
#                                           kernel_size=[3, 3],
#                                           stride=1,
#                                           padding='SAME',
#                                           data_format='NHWC', 
#                                           trainable=True,
#                                           scope='conv2_shading')
                
        net_albedo = cnnm.up_project(input_data=net, kernel_size=[3, 3], num_outputs=32, 
                                     batch_size=batch_size, scope='32x_up_projection_albedo', stride=1, 
                                     use_batch_norm=True, bn_decay=bn_decay,
                                     bn_epsilon=bn_epsilon, is_training=is_training)
        net_shading = cnnm.up_project(input_data=net, kernel_size=[3, 3], num_outputs=32, 
                                      batch_size=batch_size, scope='32x_up_projection_shading', stride=1, 
                                      use_batch_norm=True, bn_decay=bn_decay,
                                      bn_epsilon=bn_epsilon, is_training=is_training)

        with slim.arg_scope(cnnm.upproject_arg_scope(weight_decay=0.0001,
                                                     batch_norm_decay=bn_decay,
                                                     batch_norm_epsilon=bn_epsilon,
                                                     batch_norm_scale=True,
                                                     activation_fn=None,
                                                     use_batch_norm=True,
                                                     is_training=is_training)):
            with slim.arg_scope([slim.conv2d],
                                outputs_collections=end_points_collection):
                net_albedo = slim.conv2d(inputs=net_albedo,
                                         num_outputs=3,
                                         kernel_size=[3, 3],
                                         stride=1,
                                         padding='SAME',
                                         data_format='NHWC', 
                                         trainable=True,
                                         scope='out_albedo')

                net_shading = slim.conv2d(inputs=net_shading,
                                          num_outputs=3,
                                          kernel_size=[3, 3],
                                          stride=1,
                                          padding='SAME',
                                          data_format='NHWC', 
                                          trainable=True,
                                          scope='out_shading')

# conv(1, 1, 1024, 1, 1, biased=True, relu=False, name='layer1')
# 203              .batch_normalization(relu=False, name='layer1_BN')
# 204              .up_project([3, 3, 1024, 512], id = '2x', stride = 1, BN=True)
# 205              .up_project([3, 3, 512, 256], id = '4x', stride = 1, BN=True)
# 206              .up_project([3, 3, 256, 128], id = '8x', stride = 1, BN=True)
# 207              .up_project([3, 3, 128, 64], id = '16x', stride = 1, BN=True)
# 208              .dropout(name = 'drop', keep_prob = self.keep_prob)
# 209              .conv(3, 3, self.out_var, 1, 1, biased=False, relu=False, name = 'ConvPred'))



# Print name and shape of each tensor.
print("Layers")
for k, v in end_points.items():
    print('name = {}, shape = {}'.format(v.name, v.get_shape()))
    
# Print name and shape of parameter nodes  (values not yet initialized)
print("\n")
print("Parameters")
for v in slim.get_model_variables():
    print('name = {}, shape = {}'.format(v.name, v.get_shape()))

Tensor("resnet_v1_50/block4/unit_3/bottleneck_v1/Relu:0", shape=(4, 10, 10, 2048), dtype=float32)
Tensor("decoder/2x_up_projection/relu:0", shape=(4, 20, 20, 512), dtype=float32)
Layers
name = resnet_v1_50/conv1/Relu:0, shape = (4, 160, 160, 64)
name = resnet_v1_50/block1/unit_1/bottleneck_v1/shortcut/BatchNorm/cond/Merge:0, shape = (4, 80, 80, 256)
name = resnet_v1_50/block1/unit_1/bottleneck_v1/conv1/Relu:0, shape = (4, 80, 80, 64)
name = resnet_v1_50/block1/unit_1/bottleneck_v1/conv2/Relu:0, shape = (4, 80, 80, 64)
name = resnet_v1_50/block1/unit_1/bottleneck_v1/conv3/BatchNorm/cond/Merge:0, shape = (4, 80, 80, 256)
name = resnet_v1_50/block1/unit_1/bottleneck_v1/Relu:0, shape = (4, 80, 80, 256)
name = resnet_v1_50/block1/unit_2/bottleneck_v1/conv1/Relu:0, shape = (4, 80, 80, 64)
name = resnet_v1_50/block1/unit_2/bottleneck_v1/conv2/Relu:0, shape = (4, 80, 80, 64)
name = resnet_v1_50/block1/unit_2/bottleneck_v1/conv3/BatchNorm/cond/Merge:0, shape = (4, 80, 80, 256)
name = resnet_v1_

In [4]:
# save default graph in variable:
graph = tf.get_default_graph()

# plot imported graph:
plt_help.show_graph(graph.as_graph_def())

ValueError: GraphDef cannot be larger than 2GB.

In [ ]:
# to get every summary defined above we merge them to get one target:
merge_train_summaries = tf.summary.merge_all()

# define a FileWriter op which writes summaries defined above to disk:
summary_writer = tf.summary.FileWriter(graphs_dir + 
                                       'resnet_v1_50_up_project_dim_{b}x{h}x{w}x{c}'.format(b=shape[0], 
                                                                                            h=shape[1],
                                                                                            w=shape[2],
                                                                                            c=shape[3]))

# Op that initializes global variables in the graph:
# init_global = tf.global_variables_initializer()

# Create a saver.
saver = tf.train.Saver()
# Generates MetaGraphDef (this is the important saving operation. it saves
# the inference graph!):

saver.export_meta_graph(graphs_dir + 
                        'resnet_v1_50_up_project_dim_{b}x{h}x{w}x{c}'.format(b=shape[0],
                                                                             h=shape[1],
                                                                             w=shape[2],
                                                                             c=shape[3]) + 
                        '/tfmodel_inference.meta')

with tf.Session() as sess:
    # initialize all variables:
#     sess.run([init_global])
    # Adds a Graph to the event file. 
    # create summary that give output (TensorFlow op that output protocol
    # buffers containing 'summarized' data) of the built Tensorflow graph:
    summary_writer.add_graph(sess.graph)

    # # Runs to network output:
    # feed_dict = {x: np.random.random([1] + IMAGE_SHAPE), training: False}
    # model_output = sess.run(model_out, feed_dict=feed_dict)
    # s = sess.run(merge_train_summaries, feed_dict=feed_dict)
    # summary_writer.add_summary(summary=s)

    # # this saves data:
    # saver.save(sess, save_path + 'tfmodel_inference')
    # return model_output


In [5]:
batch_size = 2
img_np = np.random.rand(batch_size, 10, 15, 3)
img_tf = tf.Variable(img_np, name='image', dtype=tf.float32)

In [8]:
bn_decay = 0.999
bn_epsilon = 0.001
a = cnnm.up_project(input_data=img_tf, kernel_size=[3, 3], num_outputs=16, 
               batch_size=batch_size, scope='2x_up_projection', stride=1,
               use_batch_norm=True, bn_decay=bn_decay,
               bn_epsilon=bn_epsilon, is_training=True)
b = cnnm.up_project(input_data=a, kernel_size=[3, 3], num_outputs=16, 
               batch_size=batch_size, scope='4x_up_projection', stride=1,
               use_batch_norm=True, bn_decay=bn_decay,
               bn_epsilon=bn_epsilon, is_training=True)
c = cnnm.up_project(input_data=b, kernel_size=[3, 3], num_outputs=16, 
               batch_size=batch_size, scope='8x_up_projection', stride=1,
               use_batch_norm=True, bn_decay=bn_decay,
               bn_epsilon=bn_epsilon, is_training=True)
d = cnnm.up_project(input_data=c, kernel_size=[3, 3], num_outputs=3, 
               batch_size=batch_size, scope='16x_up_projection', stride=1, 
               use_batch_norm=True, bn_decay=bn_decay,
               bn_epsilon=bn_epsilon, is_training=True)
# e = slim.conv2d(inputs=d, 
#             num_outputs=num_outputs, 
#             kernel_size=[3, 3],
#                                              padding='SAME',
#                                              stride=1,
#                                              scope='ConvPred')
# conv(3, 3, self.out_var, stride=1, stride=1, biased=False, relu=False, name = 'ConvPred'))

print(img_tf.shape)
print(a.shape)
print(b.shape)
print(c.shape)
print(d.shape)

(2, 10, 15, 3)
(2, 20, 30, 16)
(2, 40, 60, 16)
(2, 80, 120, 16)
(2, 160, 240, 3)


# VGG 16:

In [2]:
image_size = vgg.vgg_16.default_image_size
image_size = 32 * 1
print('default image size: {}'.format(image_size))

# input for cnn:
x = tf.placeholder(dtype=tf.float32, 
                   shape=[None] + [None, None, 3], 
                   name='input')

default image size: 32


In [3]:
with tf.Graph().as_default():    
    # Create the model, use the default arg scope to configure the batch norm parameters.
    with slim.arg_scope(vgg.vgg_arg_scope()):
        scope = 'vgg_16'
        net, end_points = vgg.vgg_16(inputs=x,
                                     num_classes=None,
                                     scope=scope,
                                     is_training=False,  # irrelevant if num_classes==None
                                     dropout_keep_prob=0.5,  # irrelevant if num_classes==None
                                     spatial_squeeze=True,  # irrelevant if num_classes==None
                                     fc_conv_padding='VALID'  # irrelevant if num_classes==None
                                    )
print('# parameters in VGG-16 network: {}'.format(nnhelp.network_params()))
with tf.Graph().as_default():    
    # Create the model, use the default arg scope to configure the batch norm parameters.
    with slim.arg_scope(vgg.vgg_arg_scope()):
        is_2scales = False
        net_albedo, net_shading, end_points = vgg.vgg_16_custom(inputs=x, 
                                                                net=net, 
                                                                end_points=end_points,
                                                                is_2scales=is_2scales)
print('# parameters in VGG-16 + decoder (2scales={scale})'.format(scale=is_2scales) +
      'network: {num_param}'.format(num_param=nnhelp.network_params()))

        
# Print name and shape of each tensor.
print("Layers")
for k, v in end_points.items():
    print('name = {}, shape = {}'.format(v.name, v.get_shape()))
    
# Print name and shape of parameter nodes  (values not yet initialized)
print("\n")
print("Parameters")
for v in slim.get_model_variables():
    print('name = {}, shape = {}'.format(v.name, v.get_shape()))

# parameters in VGG-16 network: 14714688
# parameters in VGG-16 + decoder (2scales=False)network: 48822726
Layers
name = vgg_16/conv1/conv1_1/Relu:0, shape = (?, ?, ?, 64)
name = vgg_16/conv1/conv1_2/Relu:0, shape = (?, ?, ?, 64)
name = vgg_16/pool1/MaxPool:0, shape = (?, ?, ?, 64)
name = vgg_16/conv2/conv2_1/Relu:0, shape = (?, ?, ?, 128)
name = vgg_16/conv2/conv2_2/Relu:0, shape = (?, ?, ?, 128)
name = vgg_16/pool2/MaxPool:0, shape = (?, ?, ?, 128)
name = vgg_16/conv3/conv3_1/Relu:0, shape = (?, ?, ?, 256)
name = vgg_16/conv3/conv3_2/Relu:0, shape = (?, ?, ?, 256)
name = vgg_16/conv3/conv3_3/Relu:0, shape = (?, ?, ?, 256)
name = vgg_16/pool3/MaxPool:0, shape = (?, ?, ?, 256)
name = vgg_16/conv4/conv4_1/Relu:0, shape = (?, ?, ?, 512)
name = vgg_16/conv4/conv4_2/Relu:0, shape = (?, ?, ?, 512)
name = vgg_16/conv4/conv4_3/Relu:0, shape = (?, ?, ?, 512)
name = vgg_16/pool4/MaxPool:0, shape = (?, ?, ?, 512)
name = vgg_16/conv5/conv5_1/Relu:0, shape = (?, ?, ?, 512)
name = vgg_16/conv5/conv

In [4]:
# save default graph in variable:
graph = tf.get_default_graph()

# plot imported graph:
plt_help.show_graph(graph.as_graph_def())

In [5]:
# # Initialization:
# # Op that initializes global variables in the graph:
# init_global = tf.global_variables_initializer()
# # Op that initializes local variables in the graph:
# init_local = tf.local_variables_initializer()

In [5]:
# variables_to_restore = slim.get_variables_to_restore(include=[scope],
#                                                      exclude=None)

# # restore the parameters:
# init_fn = slim.assign_from_checkpoint_fn(
#     os.path.join(checkpoints_dir, 'vgg_16.ckpt'),
#     variables_to_restore)
# with tf.Session() as sess:
#     sess.run([init_global, init_local])
#     init_fn(sess)
    
#     uninitialized_vars = []
#     for var in tf.global_variables():
#         try:
#             sess.run(var)
#         except tf.errors.FailedPreconditionError:
#             uninitialized_vars.append(var)

# uninitialized_vars

In [6]:
# to get every summary defined above we merge them to get one target:
merge_train_summaries = tf.summary.merge_all()

if is_2scales:
    ext = '_narihira2015'
else:
    ext = ''
# define a FileWriter op which writes summaries defined above to disk:
summary_writer = tf.summary.FileWriter(graphs_dir + 'vgg16' + ext)

# Op that initializes global variables in the graph:
# init_global = tf.global_variables_initializer()

# Create a saver.
saver = tf.train.Saver()
# Generates MetaGraphDef (this is the important saving operation. it saves
# the inference graph!):

saver.export_meta_graph(graphs_dir + 'vgg16' + ext +'/tfmodel_inference.meta')

with tf.Session() as sess:
    # initialize all variables:
#     sess.run([init_global])
    # Adds a Graph to the event file. 
    # create summary that give output (TensorFlow op that output protocol
    # buffers containing 'summarized' data) of the built Tensorflow graph:
    summary_writer.add_graph(sess.graph)

    # # Runs to network output:
    # feed_dict = {x: np.random.random([1] + IMAGE_SHAPE), training: False}
    # model_output = sess.run(model_out, feed_dict=feed_dict)
    # s = sess.run(merge_train_summaries, feed_dict=feed_dict)
    # summary_writer.add_summary(summary=s)

    # # this saves data:
    # saver.save(sess, save_path + 'tfmodel_inference')
    # return model_output


In [7]:
# plot imported graph:
plt_help.show_graph(graph.as_graph_def())

# ResNet-50 1scale deconv_decoder:

In [3]:
tf.reset_default_graph()
image_size = resnet.resnet_v1_50.default_image_size
print('default image size: {}'.format(image_size))

# input for cnn:
x = tf.placeholder(dtype=tf.float32, 
                   shape=[None] + [None, None, 3], 
                   name='input')
is_training = tf.placeholder(dtype=tf.bool, name='is_training')

default image size: 224


In [4]:
with tf.Graph().as_default():    
    # Create the model, use the default arg scope to configure the batch norm parameters.
    with slim.arg_scope(resnet.resnet_arg_scope()):
        # 1000 classes instead of 1001.
        scope = 'resnet_v1_50'
        net, end_points = resnet.resnet_v1_50(inputs=x,
                                              num_classes=None,
                                              is_training=is_training,
                                              global_pool=False,
                                              output_stride=None,
                                              spatial_squeeze=False,
                                              reuse=None,
                                              scope=scope)
print('# parameters in ResNet-50 network: {}'.format(nnhelp.network_params()))

with tf.Graph().as_default():    
    # Create the model, use the default arg scope to configure the batch norm parameters.
    with slim.arg_scope(resnet.resnet_arg_scope()):
        net_albedo, net_shading, end_points = resnet.resnet_v1_50_custom(net=net,
                                                                         is_training=is_training,
                                                                         end_points=end_points)
print('# parameters in ResNet-50 + decoder' +
      ': {num_param}'.format(num_param=nnhelp.network_params()))

# Print name and shape of each tensor.
print("Layers")
for k, v in end_points.items():
    print('name = {}, shape = {}'.format(v.name, v.get_shape()))
    
# Print name and shape of parameter nodes  (values not yet initialized)
print("\n")
print("Parameters")
for v in slim.get_model_variables():
    print('name = {}, shape = {}'.format(v.name, v.get_shape()))

# parameters in ResNet-50 network: 23508032
# parameters in ResNet-50 + decodernetwork: 158279750
Layers
name = resnet_v1_50/conv1/Relu:0, shape = (?, ?, ?, 64)
name = resnet_v1_50/block1/unit_1/bottleneck_v1/shortcut/BatchNorm/cond/Merge:0, shape = (?, ?, ?, 256)
name = resnet_v1_50/block1/unit_1/bottleneck_v1/conv1/Relu:0, shape = (?, ?, ?, 64)
name = resnet_v1_50/block1/unit_1/bottleneck_v1/conv2/Relu:0, shape = (?, ?, ?, 64)
name = resnet_v1_50/block1/unit_1/bottleneck_v1/conv3/BatchNorm/cond/Merge:0, shape = (?, ?, ?, 256)
name = resnet_v1_50/block1/unit_1/bottleneck_v1/Relu:0, shape = (?, ?, ?, 256)
name = resnet_v1_50/block1/unit_2/bottleneck_v1/conv1/Relu:0, shape = (?, ?, ?, 64)
name = resnet_v1_50/block1/unit_2/bottleneck_v1/conv2/Relu:0, shape = (?, ?, ?, 64)
name = resnet_v1_50/block1/unit_2/bottleneck_v1/conv3/BatchNorm/cond/Merge:0, shape = (?, ?, ?, 256)
name = resnet_v1_50/block1/unit_2/bottleneck_v1/Relu:0, shape = (?, ?, ?, 256)
name = resnet_v1_50/block1/unit_3/bottl

In [4]:
# save default graph in variable:
graph = tf.get_default_graph()

# plot imported graph:
plt_help.show_graph(graph.as_graph_def())

In [6]:
# init_fn = slim.assign_from_checkpoint_fn(
#     os.path.join(checkpoints_dir, 'resnet_v1_50.ckpt'),
#     slim.get_model_variables())
# with tf.Session() as sess:
#     init_fn(sess)

In [7]:
# to get every summary defined above we merge them to get one target:
merge_train_summaries = tf.summary.merge_all()


# define a FileWriter op which writes summaries defined above to disk:
summary_writer = tf.summary.FileWriter(graphs_dir + 'resnet_v1_50')

# Op that initializes global variables in the graph:
# init_global = tf.global_variables_initializer()

# Create a saver.
saver = tf.train.Saver()
# Generates MetaGraphDef (this is the important saving operation. it saves
# the inference graph!):
saver.export_meta_graph(graphs_dir + 'resnet_v1_50' + '/tfmodel_inference.meta')

with tf.Session() as sess:
    # initialize all variables:
#     sess.run([init_global])
    # Adds a Graph to the event file. 
    # create summary that give output (TensorFlow op that output protocol
    # buffers containing 'summarized' data) of the built Tensorflow graph:
    summary_writer.add_graph(sess.graph)

    # # Runs to network output:
    # feed_dict = {x: np.random.random([1] + IMAGE_SHAPE), training: False}
    # model_output = sess.run(model_out, feed_dict=feed_dict)
    # s = sess.run(merge_train_summaries, feed_dict=feed_dict)
    # summary_writer.add_summary(summary=s)

    # # this saves data:
    # saver.save(sess, save_path + 'tfmodel_inference')
    # return model_output


# ResNet50 2 scale (narihira2015)

In [2]:
tf.reset_default_graph()
image_size = resnet.resnet_v1_50.default_image_size
print(f'default image size: {image_size}')

# input for cnn:
x = tf.placeholder(dtype=tf.float32, 
                   shape=[None] + [None, None, 3], 
                   name='input')
is_training = tf.placeholder(dtype=tf.bool, name='is_training')

default image size: 224


In [3]:
with tf.Graph().as_default():    
    # Create the model, use the default arg scope to configure the batch norm parameters.
    with slim.arg_scope(resnet.resnet_arg_scope()):
        # 1000 classes instead of 1001.
        scope = 'resnet_v1_50'
        net, end_points = resnet.resnet_v1_50(inputs=x,
                                              num_classes=None,
                                              is_training=is_training,
                                              global_pool=False,
                                              output_stride=None,
                                              spatial_squeeze=False,
                                              reuse=None,
                                              scope=scope)
        net_albedo, net_shading, end_points = resnet.resnet_v1_50_2scale_custom(inputs=x,
                                                                                net=net,
                                                                                is_training=is_training,
                                                                                end_points=end_points)

# Print name and shape of each tensor.
print("Layers")
for k, v in end_points.items():
    print('name = {}, shape = {}'.format(v.name, v.get_shape()))
    
# Print name and shape of parameter nodes  (values not yet initialized)
print("\n")
print("Parameters")
for v in slim.get_model_variables():
    print('name = {}, shape = {}'.format(v.name, v.get_shape()))

Layers
name = resnet_v1_50/conv1/Relu:0, shape = (?, ?, ?, 64)
name = resnet_v1_50/block1/unit_1/bottleneck_v1/shortcut/BatchNorm/batchnorm/add_1:0, shape = (?, ?, ?, 256)
name = resnet_v1_50/block1/unit_1/bottleneck_v1/conv1/Relu:0, shape = (?, ?, ?, 64)
name = resnet_v1_50/block1/unit_1/bottleneck_v1/conv2/Relu:0, shape = (?, ?, ?, 64)
name = resnet_v1_50/block1/unit_1/bottleneck_v1/conv3/BatchNorm/batchnorm/add_1:0, shape = (?, ?, ?, 256)
name = resnet_v1_50/block1/unit_1/bottleneck_v1/Relu:0, shape = (?, ?, ?, 256)
name = resnet_v1_50/block1/unit_2/bottleneck_v1/conv1/Relu:0, shape = (?, ?, ?, 64)
name = resnet_v1_50/block1/unit_2/bottleneck_v1/conv2/Relu:0, shape = (?, ?, ?, 64)
name = resnet_v1_50/block1/unit_2/bottleneck_v1/conv3/BatchNorm/batchnorm/add_1:0, shape = (?, ?, ?, 256)
name = resnet_v1_50/block1/unit_2/bottleneck_v1/Relu:0, shape = (?, ?, ?, 256)
name = resnet_v1_50/block1/unit_3/bottleneck_v1/conv1/Relu:0, shape = (?, ?, ?, 64)
name = resnet_v1_50/block1/unit_3/bott

In [4]:
# save default graph in variable:
graph = tf.get_default_graph()

# plot imported graph:
plt_help.show_graph(graph.as_graph_def())

In [5]:
# to get every summary defined above we merge them to get one target:
merge_train_summaries = tf.summary.merge_all()


# define a FileWriter op which writes summaries defined above to disk:
summary_writer = tf.summary.FileWriter(graphs_dir + 'resnet_v1_50')

# Op that initializes global variables in the graph:
# init_global = tf.global_variables_initializer()

# Create a saver.
saver = tf.train.Saver()
# Generates MetaGraphDef (this is the important saving operation. it saves
# the inference graph!):
saver.export_meta_graph(graphs_dir + 'resnet_v1_50_narihira2015' + '/tfmodel_inference.meta')

with tf.Session() as sess:
    # initialize all variables:
#     sess.run([init_global])
    # Adds a Graph to the event file. 
    # create summary that give output (TensorFlow op that output protocol
    # buffers containing 'summarized' data) of the built Tensorflow graph:
    summary_writer.add_graph(sess.graph)

    # # Runs to network output:
    # feed_dict = {x: np.random.random([1] + IMAGE_SHAPE), training: False}
    # model_output = sess.run(model_out, feed_dict=feed_dict)
    # s = sess.run(merge_train_summaries, feed_dict=feed_dict)
    # summary_writer.add_summary(summary=s)

    # # this saves data:
    # saver.save(sess, save_path + 'tfmodel_inference')
    # return model_output
